In [12]:
!pip install dataclasses
!pip install datasets 
!pip install transformers==3.5.0
!pip install torch
!pip install tensorboard==1.14.0


     |████████████████████████████████| 3.1 MB 17.7 MB/s eta 0:00:01


  Attempting uninstall: tensorboard
    Found existing installation: tensorboard 2.4.1
    Uninstalling tensorboard-2.4.1:
      Successfully uninstalled tensorboard-2.4.1


In [2]:
!pip install tensorflow==1.4.0
!pip install tensorboardX==1.8.0

In [3]:
import torch
from datetime import datetime
torch.cuda.empty_cache()
import subprocess
import shlex
from threading import Event

In [4]:
def run_QA_script(model_name, train_file, predict_file, gpu_batch_size, learning_rate, epochs, seq_len, stride, warmup, out_dir, results_file):
    !python run_squad_V2.py \
        --model_type=bert \
        --model_name_or_path=$model_name \
        --do_train \
        --do_eval \
        --do_lower_case \
        --version_2_with_negative \
        --train_file=$train_file \
        --predict_file=$predict_file \
        --per_gpu_train_batch_size=$gpu_batch_size \
        --learning_rate=$learning_rate \
        --num_train_epochs=$epochs \
        --max_seq_length=$seq_len \
        --doc_stride=$stride \
        --warmup_steps=$warmup \
        --save_steps=10000 \
        --output_dir $out_dir \
        --overwrite_output_dir \
        --results_file=$results_file

In [ ]:
model_name = 'bert-large-uncased'
train_file = '../Data/SQUAD/train-v2.0.json'
predict_file = '../Data/SQUAD/dev-v2.0.json'
gpu_batch_size = 4
learning_rate = 5e-5 #5e-5 is the default for Adam
epochs = 3.0 
seq_len = 384
stride = 128
warmup = int(205682 * 0.1) # 205,682 - total for squad 
out_dir = 'results/run_24_01_L/'
results_file = 'results/' + datetime.now().strftime("%Y_%m_%d-%I_%M_%S_%p")+'.txt'

#create results file
open(results_file, 'w').close()

run_QA_script(model_name, train_file, predict_file, gpu_batch_size, learning_rate, epochs, seq_len, stride, warmup, out_dir, results_file)





In [38]:
def run_QA_QUAC_script(model_name, train_file, predict_file, gpu_batch_size, learning_rate, epochs, seq_len, stride, warmup, out_dir, results_file, weight_decay):
    !python run_squad_V2.py \
        --model_type=bert \
        --model_name_or_path=$model_name \
        --do_train \
        --do_eval \
        --do_lower_case \
        --train_file=$train_file \
        --predict_file=$predict_file \
        --per_gpu_train_batch_size=$gpu_batch_size \
        --learning_rate=$learning_rate \
        --num_train_epochs=$epochs \
        --max_seq_length=$seq_len \
        --doc_stride=$stride \
        --warmup_steps=$warmup \
        --save_steps=10000 \
        --weight_decay=$weight_decay \
        --output_dir=$out_dir \
        --overwrite_output_dir \
        --results_file=$results_file \


In [ ]:
model_name = 'bert-large-uncased'
train_file = '../Data/QUAC/train_v0.2_edited.json'
predict_file = '../Data/QUAC/val_v0.2_edited.json' 
gpu_batch_size = 2 # was 4 
learning_rate = 5e-5 #5e-5 is the default for Adam
epochs = 1.0 # was 3.0
seq_len = 192 # was 384 for all others 
stride = 128
warmup = int(217754 * 0.1) # 205,682 - total for squad 
out_dir = 'results/run_08_02_L/'
results_file = 'results/' + datetime.now().strftime("%Y_%m_%d-%I_%M_%S_%p")+'.txt'

#create results file
open(results_file, 'w').close()

run_QA_QUAC_script(model_name, train_file, predict_file, gpu_batch_size, learning_rate, epochs, seq_len, stride, warmup, out_dir, results_file)


# SQUAD - Base HyperTuning 

In [5]:
from sklearn.model_selection import ParameterGrid
from datetime import datetime
import os 

In [6]:
param_grid = {"per_gpu_batch_size": [2, 4],
              "learning_rate": [2e-5, 3e-5, 5e-5],
              "num_epochs": [2, 3, 4] 
             }

grid = ParameterGrid(param_grid)


In [ ]:
model_name = 'bert-base-uncased'
train_file = '../Data/SQUAD/train-v2.0.json'
predict_file = '../Data/SQUAD/dev-v2.0.json'
seq_len = 384
stride = 128
warmup = int(205682 * 0.1) # 205,682 - total for squad 


In [ ]:
current_path = os.getcwd()
os.chdir(current_path)

for idx, combination in enumerate(grid): 
    
    print(combination)
    
    if(os.path.isfile('results/Hypertuning/SQUAD/done.txt')):
        os.remove('results/Hypertuning/SQUAD/done.txt')
    
    gpu_batch_size = combination['per_gpu_batch_size']
    learning_rate = combination['learning_rate']
    epochs = combination['num_epochs'] 
    
    out_dir = 'results/Hypertuning/SQUAD/hypertune_' + str(idx) + '/'
    results_file = 'results/Hypertuning/SQUAD/' + datetime.now().strftime("%Y_%m_%d-%I_%M_%S_%p")+'.txt'

    #create results file
    with open(results_file, 'w') as f:
        f.write("{}\n".format(combination))
    f.close()
    
    #os.system("python run_squad_V2.py --model_type=bert --model_name_or_path={} --do_train --do_eval -- version_2_with negative --train_file={} --predict_file={} --per_gpu_train_batch_size={} --learning_rate={} --num_train_epochs={} --max_seq_length=384 --doc_stride={} --warmup_steps={} --save_steps=10000 --output_dir {} --overwrite_output_dir --results_file={}".format(model_name, 
    #train_file, predict_file, gpu_batch_size, learning_rate, epochs, seq_len, stride, warmup, out_dir, results_file))
    
    run_QA_script(model_name, train_file, predict_file, gpu_batch_size, learning_rate, epochs, seq_len, stride, warmup, out_dir, results_file)
    
    while(os.path.isfile('results/Hypertuning/SQUAD/done.txt') != True):
        print("Done file does not exist")
        Event().wait(2.0) 
        

    
    

# QuAC - Base Hypertuning 

In [7]:
model_name = 'bert-base-uncased'
train_file = '../Data/QUAC/train_v0.2_edited.json'
predict_file = '../Data/QUAC/val_v0.2_edited.json' 
seq_len = 384
stride = 128
warmup = int(217754 * 0.1) # 217754 - total for quac


In [ ]:
current_path = os.getcwd()
os.chdir(current_path)

for idx, combination in enumerate(grid): 
    
    print(combination)
    
    if(os.path.isfile('results/Hypertuning/done.txt')):
        os.remove('results/Hypertuning/done.txt')
    
    gpu_batch_size = combination['per_gpu_batch_size']
    learning_rate = combination['learning_rate']
    epochs = combination['num_epochs'] 
    
    out_dir = 'results/Hypertuning/QUAC/hypertune_' + str(idx) + '/'
    results_file = 'results/Hypertuning/QUAC/' + datetime.now().strftime("%Y_%m_%d-%I_%M_%S_%p")+'.txt'

    #create results file
    with open(results_file, 'w') as f:
        f.write("{}\n".format(combination))
    f.close()
    
    
    run_QA_QUAC_script(model_name, train_file, predict_file, gpu_batch_size, learning_rate, epochs, seq_len, stride, warmup, out_dir, results_file)
    
    while(os.path.isfile('results/Hypertuning/done.txt') != True):
        print("Done file does not exist")
        Event().wait(2.0) 
        


{'learning_rate': 2e-05, 'num_epochs': 2, 'per_gpu_batch_size': 2}
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:541: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:542: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/tensorboard/compat/tensorflow_stub/dtypes.py:543: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.


03/11/2021 22:27:48 - INFO - __main__ -   ***** Running training *****
03/11/2021 22:27:48 - INFO - __main__ -     Num examples = 217754
03/11/2021 22:27:48 - INFO - __main__ -     Num Epochs = 2
03/11/2021 22:27:48 - INFO - __main__ -     Instantaneous batch size per GPU = 2
03/11/2021 22:27:48 - INFO - __main__ -     Total train batch size (w. parallel, distributed & accumulation) = 8
03/11/2021 22:27:48 - INFO - __main__ -     Gradient Accumulation steps = 1
03/11/2021 22:27:48 - INFO - __main__ -     Total optimization steps = 54440
Iteration:   0%|                                      | 0/27220 [00:00<?, ?it/s]/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/torch/nn/parallel/_functions.py:61: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '

Iteration:   1%|▏                         | 182/27220 [00:44<1:29:52,  5.01i

Iteration:   1%|▎                         | 376/27220 [01:23<1:29:20,  5.01it/s]


Iteration:   2%|▍                         | 498/27220 [01:47<1:29:00,  5.00it/s]/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/torch/optim/lr_scheduler.py:224: UserWarning: To get the last learning rate computed by the scheduler, please use `get_last_lr()`.
  warnings.warn("To get the last learning rate computed by the scheduler, "

Iteration:   2%|▌                         | 567/27220 [02:01<1:27:35,  5.07it/s]


Iteration:   3%|▋                         | 761/27220 [02:40<1:28:23,  4.99it/s]


...

Iteration:  86%|██████████████████████▍   | 11766/13610 [45:09<07:24,  4.15it/s]


Iteration:  88%|██████████████████████▊   | 11960/13610 [45:54<06:13,  4.41it/s]


Iteration:  89%|███████████████████████▏  | 12154/13610 [46:39<05:34,  4.35it/s]


Iteration:  91%|███████████████████████▌  | 12348/13610 [47:24<04:51,  4.32it/s]


Iteration:  91%|███████████████████████▋  | 12423/13610 [47:41<04:31,  4.37it/s]

## Testing QUAC for better results

In [28]:
# note: tried to up the max_length to account for longer sequences - didn't work due to the layer limitations of BERT.
# Then attempted the reduction and increase of the stride length to 64 and 256 but that produced the same results. 

# mean = 2658
# max = 9573

# next attempt: possible that BERT requires more training or larger batch sizes for QuAC data - based off two repo's 
# approach is to test larger batch sizes 8-16 and check on a larger amount of epochs 12-20 in increments of 2

# Links: 
## https://github.com/prdwb/orconvqa-release
## https://github.com/prdwb/attentive_history_selection
## https://arxiv.org/pdf/1905.05412.pdf
## https://github.com/prdwb/bert_hae
## 

In [29]:
'''testing_param_grid = {"per_gpu_batch_size": [8, 10, 12, 14, 16],
                     "learning_rate": [5e-5],
                     "num_epochs": [12, 14, 16, 18, 20],
                    }

test_grid = ParameterGrid(testing_param_grid)'''

# no real success with these params - stopped training early after 7 combinations 

In [49]:
# testing params from paper: https://arxiv.org/pdf/1905.12848v1.pdf

testing_param_grid = {"per_gpu_batch_size": [8, 12],
                      "learning_rate": [3e-5, 5e-5],
                      "num_epochs": [2, 4],
                     }

test_grid = ParameterGrid(testing_param_grid)

In [51]:
model_name = 'bert-base-uncased'
train_file = '../Data/QUAC/train_v0.2_edited_5000.json'
predict_file = '../Data/QUAC/val_v0.2_edited_5000.json' 
seq_len = 384
stride = 128
warmup = int(217754 * 0.1) # 217754 - total for quac

done_file = 'results/Hypertuning/done.txt'
folder_path = 'results/Hypertuning/QUAC/further_testing/Paper_Params/'

In [52]:
for idx, combination in enumerate(test_grid): 
    
    print(combination)
    
    if(os.path.isfile(done_file)):
        os.remove(done_file)
    
    gpu_batch_size = combination['per_gpu_batch_size']
    learning_rate = combination['learning_rate']
    epochs = combination['num_epochs'] 
    
    out_dir = folder_path + 'hypertune_' + str(idx) + '/'
    results_file = folder_path + datetime.now().strftime("%Y_%m_%d-%I_%M_%S_%p")+'.txt'

    #create results file
    with open(results_file, 'w') as f:
        f.write("{}\n".format(combination))
    f.close()
    
    
    run_QA_QUAC_script(model_name, train_file, predict_file, gpu_batch_size, learning_rate, epochs, seq_len, stride, warmup, out_dir, results_file, weight_decay)
    
    while(os.path.isfile(done_file) != True):
        print("Done file does not exist")
        Event().wait(2.0) 

{'learning_rate': 3e-05, 'num_epochs': 2, 'per_gpu_batch_size': 8, 'weight_decay': 0.01}
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:469: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:470: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:471: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.

Iteration:   4%|█▏                           | 286/6805 [01:31<31:34,  3.44it/s]


Iteration:   7%|██                           | 480/6805 [02:28<30:39,  3.44it/s]


Iteration:   7%|██                           | 498/6805 [02:33<30:21,  3.46it/s]/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/torch/optim/lr_scheduler.py:247: UserWarning: To get the last learning rate computed by the scheduler, please use `get_last_lr()`.
  warnings.warn("To get the last learning rate computed by the scheduler, "

Iteration:  10%|██▊                          | 671/6805 [03:24<30:50,  3.31it/s]


Iteration:  13%|███▋                         | 865/6805 [04:21<28:33,  3.47it/s]


...

Iteration:  96%|██████████████████████████▊ | 4354/4537 [27:19<01:09,  2.63it/s]


Epoch: 100%|████████████████████████████████████| 2/2 [57:06<00:00, 1713.15s/it]
03/23/2021 11:33:53 - INFO - __main__ -    global_step = 9075, average loss = 2.5911606688670217
03/23/2021 11:33:53 - INFO - __main__ -   Saving model checkpoint to results/Hypertuning/QUAC/further_testing/Paper_Params/hypertune_1/
[INFO|configuration_utils.py:282] 2021-03-23 11:33:53,694 >> Configuration saved in results/Hypertuning/QUAC/further_testing/Paper_Params/hypertune_1/config.json
[INFO|modeling_utils.py:740] 2021-03-23 11:33:54,409 >> Model weights saved in results/Hypertuning/QUAC/further_testing/Paper_Params/hypertune_1/pytorch_model.bin
[INFO|configuration_utils.py:411] 2021-03-23 11:33:54,429 >> loading configuration file results/Hypertuning/QUAC/further_testing/Paper_Params/hypertune_1/config.json
[INFO|configuration_utils.py:449] 2021-03-23 11:33:54,429 >> Model config BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForQuestionAnswering"
  ],
  "attentio

[INFO|modeling_utils.py:1056] 2021-03-23 11:33:58,028 >> All model checkpoint weights were used when initializing BertForQuestionAnswering.

[INFO|modeling_utils.py:1065] 2021-03-23 11:33:58,028 >> All the weights of BertForQuestionAnswering were initialized from the model checkpoint at results/Hypertuning/QUAC/further_testing/Paper_Params/hypertune_1/.
If your task is similar to the task the model of the checkpoint was trained on, you can already use BertForQuestionAnswering for predictions without further training.
[INFO|configuration_utils.py:411] 2021-03-23 11:33:58,029 >> loading configuration file results/Hypertuning/QUAC/further_testing/Paper_Params/hypertune_1/config.json
[INFO|configuration_utils.py:449] 2021-03-23 11:33:58,030 >> Model config BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,

03/23/2021 11:36:34 - WARNING - __main__ -   Process rank: -1, device: cuda, n_gpu: 4, distributed training: False, 16-bits training: False
[INFO|configuration_utils.py:413] 2021-03-23 11:36:35,002 >> loading configuration file https://huggingface.co/bert-base-uncased/resolve/main/config.json from cache at /home/ec2-user/.cache/torch/transformers/3c61d016573b14f7f008c02c4e51a366c67ab274726fe2910691e2a761acf43e.637c6035640bacb831febcc2b7f7bee0a96f9b30c2d7e9ef84082d9f252f3170
[INFO|configuration_utils.py:449] 2021-03-23 11:36:35,003 >> Model config BertConfig {
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "type_vocab_si

KeyboardInterrupt: 